In [ ]:
import Metashape
from pathlib import Path
import geopandas as gpd
import pandas as pd
import numpy as np
from shapely.geometry import Point, LineString
from Metashape import Shape 


In [ ]:
metashape_path = Path(r"..\metashape\Konusdalen_West.psx")

In [ ]:
doc = Metashape.Document()
doc.open(str(metashape_path))
chunk = doc.chunk
shapes = chunk.shapes

In [ ]:
line = [{"geometry":LineString([v for v in d.vertices])} for d in shapes if d.type == Shape.Type.Polyline]
line_32633 = [{"geometry_epsg:32633":LineString([chunk.orthomosaics[0].projection.transform(v, chunk.orthomosaic.projection, chunk.orthomosaics[1].projection) for v in d.vertices])} for d in shapes if d.type == Shape.Type.Polyline]
layer = [{"LAYER":d.group.label} for d in shapes if d.type == Shape.Type.Polyline]
label = [{"NAME":d.label} for d in shapes if d.type == Shape.Type.Polyline]
attributes = [dict(d.attributes) for d in shapes if d.type == Shape.Type.Polyline]


In [ ]:
t = pd.DataFrame.from_records(layer)

In [ ]:
for mdata in [label, attributes, line]:
    t = t.merge(t.from_records(mdata), left_index=True, right_index=True)
    
t = t[~t.LAYER.str.contains("Contours")].reset_index(drop=True)

In [ ]:
df = gpd.GeoDataFrame(t.copy(), crs="EPSG:4978") #(change epsg)
df.to_file(Path(metashape_path.parent.parent, "export", "shapes", "Shapes_localcrs_epsg4978.gpkg"), driver='GPKG')

In [ ]:
df.plot()